In [1]:
%cd /ibex/user/slimhy/PADS/code/
# %env CUDA_LAUNCH_BLOCKING=1
"""
Extracting features into HDF5 files for each split.
"""
import argparse
import torch
import numpy as np

from datasets.shapeloaders import CoMPaTManifoldDataset, ShapeNetDataset
from datasets.metadata import (
    get_compat_transform,
    get_shapenet_transform,
)
from datasets.metadata import SHAPENET_NAME_TO_SYNSET

import trimesh

import util.misc as misc
import util.s2vs as s2vs
from util.misc import d_GPU, show_side_by_side

/ibex/user/slimhy/PADS/code


In [2]:
def get_args_parser():
    parser = argparse.ArgumentParser("Extracting Features", add_help=False)

    # Model parameters
    parser.add_argument(
        "--batch_size",
        default=32,
        type=int,
        help="Batch size per GPU (effective batch size is batch_size * accum_iter * # gpus",
    )
    parser.add_argument(
        "--text_model_name",
        type=str,
        help="Text model name to use",
    )
    parser.add_argument(
        "--ae",
        type=str,
        metavar="MODEL",
        help="Name of autoencoder",
    )
    parser.add_argument(
        "--ae-latent-dim",
        type=int,
        default=512*8,
        help="AE latent dimension",
    )
    parser.add_argument(
        "--ae_pth",
        required=True,
        help="Autoencoder checkpoint"
    )
    parser.add_argument(
        "--point_cloud_size",
        default=2048,
        type=int,
        help="input size"
    )
    parser.add_argument(
        "--fetch_keys",
        action="store_true",
        default=False,
    )
    parser.add_argument(
        "--use_embeds",
        action="store_true",
        default=False,
    )
    parser.add_argument(
        "--intensity_loss",
        action="store_true",
        default=False,
        help="Contrastive edit intensity loss using ground-truth labels.",
    )

    # Dataset parameters
    parser.add_argument(
        "--dataset",
        type=str,
        choices=["graphedits"],
        help="dataset name",
    )
    parser.add_argument(
        "--data_path",
        type=str,
        help="dataset path",
    )
    parser.add_argument(
        "--data_type",
        type=str,
        help="dataset type",
    )
    parser.add_argument(
        "--max_edge_level",
        default=None,
        type=int,
        help="maximum edge level to use",
    )
    parser.add_argument(
        "--device", default="cuda", help="device to use for training / testing"
    )
    parser.add_argument("--seed", default=0, type=int)
    parser.add_argument("--num_workers", default=60, type=int)
    parser.add_argument(
        "--pin_mem",
        action="store_true",
        help="Pin CPU memory in DataLoader for more efficient (sometimes) transfer to GPU.",
    )

    return parser

# Set dummy arg string to debug the parser
call_string = """--ae_pth ckpt/ae_m512.pth \
    --ae kl_d512_m512_l8 \
    --ae-latent-dim 4096 \
    --batch_size 32 \
    --num_workers 8 \
    --device cuda"""
    

# Parse the arguments
args = get_args_parser()
args = args.parse_args(call_string.split())

# Set device and seed
device = torch.device(args.device)
misc.set_all_seeds(args.seed)
torch.backends.cudnn.benchmark = True

# Instantiate autoencoder
ae = s2vs.load_model(args.ae, args.ae_pth, device, torch_compile=True)
ae = ae.eval()

Set seed to 0
Loading autoencoder [ckpt/ae_m512.pth].


In [3]:
def get_rec_mesh(ae, points, device):
    points = points.to(device)
    init_latents = s2vs.encode_pc(ae, points)
    return s2vs.decode_latents(ae, d_GPU(init_latents), grid_density=256, batch_size=128**3)

def get_stuff(surface_points):
    # Get pc bounding box following each axis
    min_x = surface_points[:, :, 0].min()
    max_x = surface_points[:, :, 0].max()
    min_y = surface_points[:, :, 1].min()
    max_y = surface_points[:, :, 1].max()
    min_z = surface_points[:, :, 2].min()
    max_z = surface_points[:, :, 2].max()

    # Compute extents
    extents = [d.item() for d in [max_x - min_x, max_y - min_y, max_z - min_z]]
    return np.array(extents)

def flip_front_to_right(pc):
    """
    Rotate 90° around Y axis (from front-facing to right-facing).
    """
    full_transform = torch.tensor(
        [[0.0, 0.0, -1.0], [0.0, 1.0, 0.0], [1.0, 0.0, 0.0]],
        dtype=torch.float32,
        device=pc.device,
    )
    return torch.matmul(pc.squeeze(), full_transform).unsqueeze(0)

def get_datasets(active_class):
    shapenet_dataset = ShapeNetDataset(
        dataset_folder="/ibex/project/c2273/ShapeNet/",
        shape_cls=SHAPENET_NAME_TO_SYNSET[active_class],
        pc_size=2048,
    )

    compat_dataset = CoMPaTManifoldDataset(
        "/ibex/project/c2273/3DCoMPaT/manifold/",
        active_class,
        2048,
        normalize=False,
        sampling_method="surface",
        recenter_mesh=True,
        process_mesh=True
    )

    compat_dataset_transformed = CoMPaTManifoldDataset(
        "/ibex/project/c2273/3DCoMPaT/manifold/",
        active_class,
        2048,
        normalize=False,
        sampling_method="surface",
        recenter_mesh=True,
        process_mesh=True,
        scale_to_shapenet=True,
        align_to_shapenet=True
    )
    
    return shapenet_dataset, compat_dataset, compat_dataset_transformed

def get_points(dataset, transform=None, is_compat=False, obj_k=0):
    if is_compat:
        surface_points, _ = next(dataset[obj_k])
        return surface_points
    else:
        surface_points, _ = dataset[obj_k]
        return transform(surface_points)

In [4]:
active_class = "bed"
shapenet_dataset, compat_dataset, compat_dataset_transformed = get_datasets(active_class)
shapenet_transform = get_shapenet_transform(active_class)

shapenet_points = get_points(shapenet_dataset, shapenet_transform)
compat_points = get_points(compat_dataset, is_compat=True)
compat_points_transformed = get_points(compat_dataset_transformed, is_compat=True)

In [5]:
shapenet_mesh = get_rec_mesh(ae, shapenet_points, device)
compat_mesh = get_rec_mesh(ae, compat_points, device)
compat_mesh_transformed = get_rec_mesh(ae, compat_points_transformed, device)

show_side_by_side(shapenet_mesh, compat_mesh, compat_mesh_transformed)

In [6]:
import numpy as np
from scipy import interpolate

def match_distributions(A, B):
    A = np.array(A)
    B = np.array(B)
    
    # Sort both sets
    A_sorted = np.sort(A)
    B_sorted = np.sort(B)
    
    # Calculate CDFs
    A_cdf = np.arange(1, len(A) + 1) / len(A)
    B_cdf = np.arange(1, len(B) + 1) / len(B)
    
    # Create interpolation function for B
    f = interpolate.interp1d(B_cdf, B_sorted, kind='linear', fill_value='extrapolate')
    
    # Find corresponding values in B for each point in A
    A_matched = f(A_cdf)
    
    # Calculate scale factors
    scale_factors = A_matched / A_sorted
    
    # Create a dictionary to map original A values to their scale factors
    scale_dict = dict(zip(A_sorted, scale_factors))
    
    # Return scale factors in the original order of A
    return np.array([scale_dict[a] for a in A])

# Example usage
A = [1, 5, 2, 8, 3]
B = [10, 20, 30, 40, 50, 60, 70]

scale_factors = match_distributions(A, B)
print("Scale factors:", scale_factors)
print("Original A:", A)
print("Transformed A:", np.array(A) * scale_factors)
print("B:", B)


Scale factors: [14.   11.2  14.    8.75 14.  ]
Original A: [1, 5, 2, 8, 3]
Transformed A: [14. 56. 28. 70. 42.]
B: [10, 20, 30, 40, 50, 60, 70]
